In [1]:
import numpy as np
import matplotlib
import matplotlib.pyplot as plt
import glob
import pandas as pd

import matplotlib
import matplotlib.cm as cm
from matplotlib.colors import BoundaryNorm
import datetime as dt

from mpl_toolkits.axes_grid1 import make_axes_locatable
import math
import matplotlib.image as mgimg
from collections import Counter
import scipy.optimize as opt
from sklearn.svm import SVC
import plotly.graph_objects as go
from sklearn.metrics import jaccard_score

# Opens the Dataset Collected from the Range Monitor

In [2]:
f = open("Compare_In_Out_Subs_CAPE.txt", "r") #import file with data in it
unpack = np.loadtxt(f, unpack = True, usecols=(0,1,2,3,4,5,6)) #convert data into unpacking info
#avoid some of the rows that use strings
psl = unpack[2] #unpack pressure for each point
cape_inner = unpack[3] #unpack the CAPE values inside the storms
cape_outer = unpack[4] #unpack CAPE values outside of the storms
subs_inner = unpack[5] #repeat for subsaturation
subs_outer = unpack[6]

# Allows the SVM to be Able to Use the Data

In [3]:
yes = np.ones(np.shape(psl)) #since we want a decision boundary
no = np.zeros(np.shape(psl))
decision = np.concatenate((yes,no),axis=None) #since the inner values will be first in the combined array
cape_all = np.concatenate((cape_inner,cape_outer),axis=None) #for the CAPE
subs_all = np.concatenate((subs_inner,subs_outer),axis=None) #for the subsaturation
psl_all = np.concatenate((psl,psl),axis=None) #for pressure
allarray=np.vstack((cape_all, subs_all, psl_all)) #creating a 3 stack array so I can manipulate it for the classifier
trueallarray=allarray.T #transpose so it matches that shape of the decision array

# Initial Plotting of the Data

In [5]:
reds = decision == 1 #for values inside of the storm
blues = decision == 0 #for values outside of the storm


fig = go.Figure(data=[go.Scatter3d(x=cape_all[reds],
                                   y=subs_all[reds],
                                   z=psl_all[reds],
                                   mode='markers',
                                   name = 'Inside TS Force Winds',
                                   marker=dict(size=2, color='red')),
                      go.Scatter3d(x=cape_all[blues],
                                   y=subs_all[blues],
                                   z=psl_all[blues],
                                   mode='markers',
                                   name = '2.5 Degrees Outside of TS Force Winds',
                                   marker=dict(size=2, color='blue'))
                      ])
fig.update_layout(title="Subsat/CAPE/Min PSL For Inside/Outside of TS Winds For Atl. Storms (2002-2013)",scene=dict(
                             xaxis_title="CAPE [K]",
                             yaxis_title="Subsaturation [K]",
                             zaxis_title="Minimal Pressure [hPa]"))
#this is the combined values each into one array and spliced
fig.show()

# The Actual SVM Algorithm

In [14]:
sv_fit = SVC(C=1,kernel='linear',tol=1e-3) #creating the support vector machine
mySVM=sv_fit.fit(trueallarray,decision) #fitting the SVM
svs = mySVM.support_vectors_ #for the support vectors
z = lambda x,y: (-mySVM.intercept_[0]-mySVM.coef_[0][0]*x-mySVM.coef_[0][1]*y) / mySVM.coef_[0][2]
#for the decision boundary in 3D
print("The shape of the support vectors is {}.".format(svs.shape)) #get the amount of support vectors
print("The equation relating pressure, CAPE, and substauration is (- {:.2f} - {:.2f}*CAPE - {:.2f}*SUBSAT)/{:.2f} = Pressure".format(mySVM.intercept_[0],mySVM.coef_[0][0],mySVM.coef_[0][1],mySVM.coef_[0][2]))

The shape of the support vectors is (1515, 3).
The equation relating pressure, CAPE, and substauration is (- 29.99 - -0.07*CAPE - -0.88*SUBSAT)/-0.02 = Pressure


# Calculating the Accuracy of the SVM Classifier

In [15]:
hit_rate = [] #I want to get the accuracy of the decision boundary
for_inner=[]
for_outer=[]
yes_check = np.concatenate((yes,yes),axis=None) #due to the jaccard not working well for detecting misses
for r in range(len(cape_inner)):
    if (z(cape_inner[r],subs_inner[r]) > psl[r]):
        hit_rate.append(1) #1 if it on the correct side of the decision boundary
        for_inner.append(1) #if I want the jaccard score of just inner or outter
    else:
        hit_rate.append(0)
        for_inner.append(0) #0 if it is on the incorrect side of the decision boundary
for r in range(len(cape_outer)):
    if (z(cape_outer[r],subs_outer[r]) < psl[r]):
        hit_rate.append(1) #1 if it is on the correct side of the decision boundary, should be 0 but the jaccard score doesn't work well
        for_outer.append(1) #flip since it doesn't work well for 0 values
    else:
        hit_rate.append(0) #0 if it is on the incorrect side of the decision boundary, should be 1 but the jaccard score doesn't work well
        for_outer.append(0) #flip since it doesn't work well for 0 values
accuracy=jaccard_score(yes_check, hit_rate) #compares calculated values to actual values
print("The accuracy for predicting inner values: {}".format(jaccard_score(yes, for_inner)))
print("The accuracy for predicting outer values: {}".format(jaccard_score(yes, for_outer)))
print("The overall acurracy of the decision boundary: {}".format(accuracy))

The accuracy for predicting inner values: 0.823237885462555
The accuracy for predicting outer values: 0.7973568281938326
The overall acurracy of the decision boundary: 0.8102973568281938


# Plot with the Support Vectors Alone

In [63]:
reds = decision == 1
blues = decision == 0


fig = go.Figure(data=[go.Scatter3d(x=cape_all[reds],
                                   y=subs_all[reds],
                                   z=psl_all[reds],
                                   mode='markers',
                                   name = 'Inside TS Force Winds',
                                   marker=dict(size=2, color='red')),
                      go.Scatter3d(x=cape_all[blues],
                                   y=subs_all[blues],
                                   z=psl_all[blues],
                                   mode='markers',
                                   name = '2.5 Degrees Outside of TS Force Winds',
                                   marker=dict(size=2, color='blue')),
                      go.Scatter3d(x=svs[:, 0], #using the SVM, CAPE
                                   y=svs[:, 1], #using the SVM, Subsaturation
                                   z=svs[:, 2], #using the SVM, pressure
                                   mode='markers',
                                   name = 'Support Vectors',
                                   marker=dict(size=4, color='black'))
                      ])
fig.update_layout(title="Subsat/CAPE/Min PSL For Inside/Outside of TS Winds For Atl. Storms (2002-2013)",scene=dict(
                             xaxis_title="CAPE [K]",
                             yaxis_title="Subsaturation [K]",
                             zaxis_title="Minimal Pressure [hPa]"))

# Plot with Decision Boundary Alone (Reduced to be Within Bounds)

In [61]:
reds = decision == 1
blues = decision == 0


fig = go.Figure(data=[go.Scatter3d(x=cape_all[reds],
                                   y=subs_all[reds],
                                   z=psl_all[reds],
                                   mode='markers',
                                   name = 'Inside TS Force Winds',
                                   marker=dict(size=2, color='red')),
                      go.Scatter3d(x=cape_all[blues],
                                   y=subs_all[blues],
                                   z=psl_all[blues],
                                   mode='markers',
                                   name = '2.5 Degrees Outside of TS Force Winds',
                                   marker=dict(size=2, color='blue')),
                      go.Mesh3d(x=trueallarray[:,0], #takes the x value of the DB
                                   y=trueallarray[:,1], #takes the y value of the DB
                                   z=z(trueallarray[:,0],trueallarray[:,1]), #uses the z frunction from above to create a DB
                                   color="green",
                                   name = 'Decision Boundary, Accuracy: {:.2f}%'.format(100*accuracy)
                                  )])
fig.update_layout(title="Subsat/CAPE/Min PSL For Inside/Outside of TS Winds For Atl. Storms (2002-2013)",scene=dict(
                             xaxis_title="CAPE [K]",
                             yaxis_title="Subsaturation [K]",
                             zaxis_title="Minimal Pressure [hPa]"))
fig.update_layout(
    scene = dict(zaxis = dict(range=[930,1020],),))
fig.update_traces(showlegend=True, selector=dict(type='mesh3d'))

# Decision Boundary Without Pressure Bounds

In [62]:
reds = decision == 1
blues = decision == 0


fig = go.Figure(data=[go.Scatter3d(x=cape_all[reds],
                                   y=subs_all[reds],
                                   z=psl_all[reds],
                                   mode='markers',
                                   name = 'Inside TS Force Winds',
                                   marker=dict(size=2, color='red')),
                      go.Scatter3d(x=cape_all[blues],
                                   y=subs_all[blues],
                                   z=psl_all[blues],
                                   mode='markers',
                                   name = '2.5 Degrees Outside of TS Force Winds',
                                   marker=dict(size=2, color='blue')),
                      go.Mesh3d(x=trueallarray[:,0], #takes the x value of the DB
                                   y=trueallarray[:,1], #takes the y value of the DB
                                   z=z(trueallarray[:,0],trueallarray[:,1]), #uses the z frunction from above to create a DB
                                   color="green",
                                   name = 'Decision Boundary, Accuracy: {:.2f}%'.format(100*accuracy)
                                  )])
fig.update_layout(title="Subsat/CAPE/Min PSL For Inside/Outside of TS Winds For Atl. Storms (2002-2013)",scene=dict(
                             xaxis_title="CAPE [K]",
                             yaxis_title="Subsaturation [K]",
                             zaxis_title="Minimal Pressure [hPa]"))

fig.update_traces(showlegend=True, selector=dict(type='mesh3d'))

# The Decision Boundary and the Support Vectors Together

In [65]:
reds = decision == 1
blues = decision == 0


fig = go.Figure(data=[go.Scatter3d(x=cape_all[reds],
                                   y=subs_all[reds],
                                   z=psl_all[reds],
                                   mode='markers',
                                   name = 'Inside TS Force Winds',
                                   marker=dict(size=2, color='red')),
                      go.Scatter3d(x=cape_all[blues],
                                   y=subs_all[blues],
                                   z=psl_all[blues],
                                   mode='markers',
                                   name = '2.5 Degrees Outside of TS Force Winds',
                                   marker=dict(size=2, color='blue')),
                      go.Scatter3d(x=svs[:, 0], #using the SVM, CAPE
                                   y=svs[:, 1], #using the SVM, Subsaturation
                                   z=svs[:, 2], #using the SVM, pressure
                                   mode='markers',
                                   name = 'Support Vectors',
                                   marker=dict(size=4, color='black')),
                      go.Mesh3d(x=trueallarray[:,0], #takes the x value of the DB
                                   y=trueallarray[:,1], #takes the y value of the DB
                                   z=z(trueallarray[:,0],trueallarray[:,1]), #uses the z frunction from above to create a DB
                                   color="green",
                                   name = 'Decision Boundary, Accuracy: {:.4f}%'.format(100*accuracy)
                                  )])
fig.update_layout(title="Subsat/CAPE/Min PSL For Inside/Outside of TS Winds For Atl. Storms (2002-2013)",scene=dict(
                             xaxis_title="CAPE [K]",
                             yaxis_title="Subsaturation [K]",
                             zaxis_title="Minimal Pressure [hPa]"))
fig.update_layout(
    scene = dict(zaxis = dict(range=[930,1020],),))
fig.update_traces(showlegend=True, selector=dict(type='mesh3d'))